In [ ]:
!pip install transformers datasets stanza

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.2/491.2 kB 9.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 39.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.9/183.9 kB 17.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 14.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 103.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 89.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 58.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 4.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 42.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
!unzip lessons_final.zip -d lessons_final

Archive:  lessons_final.zip
   creating: lessons_final/lessons_final/
  inflating: lessons_final/lessons_final/v1_l1.pkl  
  inflating: lessons_final/lessons_final/v1_l10.pkl  
  inflating: lessons_final/lessons_final/v1_l100.pkl  
  inflating: lessons_final/lessons_final/v1_l101.pkl  
  inflating: lessons_final/lessons_final/v1_l102.pkl  
  inflating: lessons_final/lessons_final/v1_l103.pkl  
  inflating: lessons_final/lessons_final/v1_l104.pkl  
  inflating: lessons_final/lessons_final/v1_l105.pkl  
  inflating: lessons_final/lessons_final/v1_l106.pkl  
  inflating: lessons_final/lessons_final/v1_l107.pkl  
  inflating: lessons_final/lessons_final/v1_l108.pkl  
  inflating: lessons_final/lessons_final/v1_l109.pkl  
  inflating: lessons_final/lessons_final/v1_l11.pkl  
  inflating: lessons_final/lessons_final/v1_l110.pkl  
  inflating: lessons_final/lessons_final/v1_l111.pkl  
  inflating: lessons_final/lessons_final/v1_l112.pkl  
  inflating: lessons_final/lessons_final/v1_l113.pkl  

# Pretraining

In [ ]:
import os
import pickle
import random
import torch
import stanza
import torch.nn as nn
from datasets import Dataset
from transformers import (
    T5Tokenizer, T5Config, Trainer, TrainingArguments,
    T5ForConditionalGeneration
)
from transformers import EarlyStoppingCallback

# ──────── Device ────────
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# ──────── Stanza setup ────────
stanza.download("en", verbose=False)
nlp = stanza.Pipeline(
    lang="en",
    processors="tokenize,pos,lemma,depparse,ner",
    tokenize_no_ssplit=True,
    use_gpu=torch.cuda.is_available()
)

# ──────── Combo‑ID utils ────────
combo2id = {}
combo_counter = 1
MAX_COMBO_ID = 1024
UNKNOWN_COMBO_ID = 0

def get_combo_id(pos, dep, ner, morph):
    global combo_counter
    key = (pos, dep, ner, morph)
    if key not in combo2id:
        if combo_counter >= MAX_COMBO_ID:
            return UNKNOWN_COMBO_ID
        combo2id[key] = combo_counter
        combo_counter += 1
    return combo2id[key]

def get_char_offset_ner_map(doc):
    ner_map = {}
    for ent in doc.ents:
        for i in range(ent.start_char, ent.end_char):
            ner_map[i] = ent.type
    return ner_map

def extract_combo_ids_from_doc(doc, tokenizer, max_len=256):
    ner_map = get_char_offset_ner_map(doc)
    combo_ids = []
    for sent in doc.sentences:
        for word in sent.words:
            pos   = word.upos or "X"
            dep   = word.deprel or "dep"
            morph = word.feats or ""
            start = word.start_char or 0
            ner   = ner_map.get(start, "O")
            cid   = get_combo_id(pos, dep, ner, morph)
            sub_len = len(tokenizer(word.text).input_ids) - 1
            combo_ids.extend([cid] * sub_len)
    return combo_ids[:max_len]

# ──────── Simple span‑masking ────────
def simple_t5_mask(text):
    words = text.strip().split()
    if len(words) < 4:
        return text, text
    span_len = random.randint(1, min(3, len(words) - 1))
    start = random.randint(0, len(words) - span_len)
    masked = words[:start] + ["<extra_id_0>"] + words[start + span_len:]
    masked_text = " ".join(masked)
    target_text = "<extra_id_0> " + " ".join(words[start:start + span_len])
    return masked_text, target_text

# ──────── Model ────────
class SyntaxT5(T5ForConditionalGeneration):
    def __init__(self, config, combo_vocab_size=MAX_COMBO_ID):
        super().__init__(config)
        self.shared       = nn.Embedding(config.vocab_size, config.d_model)
        self.encoder.embed_tokens = self.shared
        self.decoder.embed_tokens = self.shared
        self.combo_embed  = nn.Embedding(combo_vocab_size, config.d_model)
        self.fuse_proj    = nn.Linear(2 * config.d_model, config.d_model)
        self.stored_combo_ids = None

    def prepare_inputs_for_generation(
        self, input_ids, past_key_values=None, attention_mask=None,
        use_cache=None, encoder_outputs=None, **kwargs
    ):
        full_combo = self.stored_combo_ids
        if past_key_values is None:
            combo_ids = full_combo
        else:
            combo_ids = full_combo[:, -1].unsqueeze(-1)
        return {
            "decoder_input_ids":  input_ids,
            "attention_mask":     attention_mask,
            "encoder_outputs":    encoder_outputs,
            "past_key_values":    past_key_values,
            "use_cache":          use_cache,
            "combo_ids":          combo_ids,
        }

    def forward(
        self, input_ids=None, inputs_embeds=None, attention_mask=None,
        decoder_input_ids=None, decoder_attention_mask=None,
        encoder_outputs=None, past_key_values=None, labels=None,
        use_cache=None, **kwargs
    ):
        # generation path
        if encoder_outputs is not None:
            return super().forward(
                encoder_outputs=encoder_outputs,
                past_key_values=past_key_values,
                attention_mask=attention_mask,
                decoder_input_ids=decoder_input_ids,
                decoder_attention_mask=decoder_attention_mask,
                labels=labels,
                use_cache=use_cache
            )
        # training/encode path
        combo_ids = kwargs.get("combo_ids", self.stored_combo_ids)
        if combo_ids is None and input_ids is not None:
            combo_ids = torch.zeros_like(input_ids)
        tok_emb = inputs_embeds if inputs_embeds is not None else self.shared(input_ids)
        cmb_emb = self.combo_embed(combo_ids.to(tok_emb.device))
        fused  = torch.cat([tok_emb, cmb_emb], dim=-1)
        inputs_embeds = self.fuse_proj(fused)
        return super().forward(
            inputs_embeds=inputs_embeds,
            attention_mask=attention_mask,
            decoder_input_ids=decoder_input_ids,
            decoder_attention_mask=decoder_attention_mask,
            labels=labels,
            use_cache=use_cache,
            past_key_values=past_key_values
        )

# ──────── Data Collator ────────
class DataCollatorWithCombo:
    def __init__(self, tokenizer):
        self.tokenizer = tokenizer

    def __call__(self, batch):
        return {
            "input_ids":      torch.tensor([ex["input_ids"]      for ex in batch], dtype=torch.long),
            "attention_mask": torch.tensor([ex["attention_mask"] for ex in batch], dtype=torch.long),
            "labels":         torch.tensor([ex["labels"]         for ex in batch], dtype=torch.long),
            "combo_ids":      torch.tensor([ex["combo_ids"]      for ex in batch], dtype=torch.long),
        }

# ──────── Preprocess ────────
def preprocess(example, tokenizer):
    src = tokenizer(
        example["input"],
        padding="max_length",
        truncation=True,
        max_length=256
    )
    tgt = tokenizer(
        example["output"],
        padding="max_length",
        truncation=True,
        max_length=64
    )
    combo = example["combo_ids"]
    combo += [UNKNOWN_COMBO_ID] * (256 - len(combo))
    src["combo_ids"] = combo[:256]
    src["labels"]    = [
        t if t != tokenizer.pad_token_id else -100
        for t in tgt["input_ids"]
    ]
    return src

# ──────── Prediction Cleaning ────────
def clean_prediction(raw_pred, tokenizer):
    return raw_pred.replace(tokenizer.pad_token, "")\
                   .replace(tokenizer.eos_token, "")\
                   .strip()

# ──────── Evaluation ────────
def evaluate(model, tokenizer, dataset):
    model.eval()
    correct = 0
    for ex in dataset:
        inp  = ex["input"]
        gold = ex["output"].strip()
        enc = tokenizer(
            inp, return_tensors="pt",
            padding=True, truncation=True, max_length=256
        ).to(device)
        combo = ex["combo_ids"] + [UNKNOWN_COMBO_ID] * (256 - len(ex["combo_ids"]))
        model.stored_combo_ids = torch.tensor([combo], device=device)
        with torch.no_grad():
            out_ids = model.generate(
                input_ids=enc["input_ids"],
                attention_mask=enc["attention_mask"],
                max_new_tokens=20,
                do_sample=False,
                use_cache=True
            )
        raw  = tokenizer.decode(out_ids[0], skip_special_tokens=False)
        pred = clean_prediction(raw, tokenizer)
        if pred == gold:
            correct += 1
    print(f"✅ Eval Accuracy: {correct}/{len(dataset)} = {correct/len(dataset):.2f}")
    torch.cuda.empty_cache()

# ──────── Training per‐level ────────
def train_level(dataset, tokenizer, model, args, level):
    print(f"\n🔁 Training curriculum level {level}")
    tokenized = dataset.map(
        lambda ex: preprocess(ex, tokenizer),
        remove_columns=["input", "output", "combo_ids"]
    )
    split_dataset = tokenized.train_test_split(test_size=0.05, seed=42)
    train_set = split_dataset['train']
    eval_set = split_dataset['test']
    print(f"{len(train_set)} train | {len(eval_set)} val")
    trainer = Trainer(
        model=model,
        args=args,
        train_dataset=train_set,
        eval_dataset=eval_set,
        tokenizer=tokenizer,
        callbacks=[
            EarlyStoppingCallback(
                early_stopping_patience=3,
                early_stopping_threshold=0.0
            )
        ],
        data_collator=DataCollatorWithCombo(tokenizer)
    )
    trainer.train()
    del trainer
    torch.cuda.empty_cache()

# ──────── Setup model/tokenizer/args ────────
tokenizer = T5Tokenizer.from_pretrained("t5-base")
config    = T5Config.from_pretrained("t5-base")
model     = SyntaxT5(config=config, combo_vocab_size=MAX_COMBO_ID).to(device)

args = TrainingArguments(
    per_device_train_batch_size=16,
    num_train_epochs=10,
    logging_strategy="epoch",
    report_to="none",

    # do evaluation & checkpointing every epoch
    eval_strategy="epoch",
    save_strategy="epoch",
    save_total_limit=1,
    # automatically reload best checkpoint
    load_best_model_at_end=True,
    metric_for_best_model="eval_loss",
    greater_is_better=False,

    remove_unused_columns=False,
    output_dir="./t5_syntax_curriculum",
    # per_device_train_batch_size=16,
    # num_train_epochs=10,
    # save_total_limit=1,
    # # logging_steps=5,
    # logging_strategy="epoch",
    # report_to="none",
    # eval_strategy="epoch",     # ← Evaluate every epoch
    # save_strategy="epoch",           # (optional) Save checkpoint every epoch
    # remove_unused_columns=False
)

# ──────── Build curriculum from your lesson files ────────
pkl_folder = "./lessons_final/lessons_final"
curriculum = []

import re

def extract_vol_lesson(filename):
    match = re.match(r'v(\d+)_l(\d+)\.pkl', filename)
    return (int(match.group(1)), int(match.group(2))) if match else (999, 999)

all_files = os.listdir(pkl_folder)
pkl_files = sorted(
    [f for f in all_files if re.match(r'v\d+_l\d+\.pkl', f)],
    key=extract_vol_lesson
)

for fname in pkl_files:
    if not fname.endswith(".pkl"):
        continue
    with open(os.path.join(pkl_folder, fname), "rb") as f:
        docs = pickle.load(f)  # list of stanza.Document
    examples = []
    for d in docs:
        masked, target = simple_t5_mask(d.text)
        combo_ids = extract_combo_ids_from_doc(d, tokenizer, max_len=256)
        examples.append({
            "input":     masked,
            "output":    target,
            "combo_ids": combo_ids
        })
    ds = Dataset.from_list(examples)
    curriculum.append((fname, ds))
    print(f"✅ Loaded {fname} ({len(examples)} examples)")

# ──────── Run curriculum ────────
for i, (lesson_name, level_ds) in enumerate(curriculum, start=1):
    # if i==3: break
    print(f"▶︎ Lesson {lesson_name}")
    train_level(level_ds, tokenizer, model, args, i)

# ──────── Final quick test ────────
def generate(text):
    model.eval()
    enc = tokenizer(
        text, return_tensors="pt",
        padding=True, truncation=True, max_length=256
    ).to(device)
    combo = extract_combo_ids_from_doc(nlp(text), tokenizer, max_len=256)
    combo += [UNKNOWN_COMBO_ID] * (256 - len(combo))
    model.stored_combo_ids = torch.tensor([combo], device=device)
    with torch.no_grad():
        out_ids = model.generate(
            input_ids=enc["input_ids"],
            attention_mask=enc["attention_mask"],
            max_new_tokens=20,
            do_sample=False,
            use_cache=True
        )
    raw = tokenizer.decode(out_ids[0], skip_special_tokens=False)
    return clean_prediction(raw, tokenizer)

print("\n🧪 Final Test Generation:")
test_text = "They are <extra_id_0> the car at the <extra_id_1>."
print("INPUT :", test_text)
print("OUTPUT:", generate(test_text))


Using device: cuda
✅ Loaded v1_l1.pkl (8 examples)
✅ Loaded v1_l2.pkl (8 examples)
✅ Loaded v1_l3.pkl (13 examples)
✅ Loaded v1_l4.pkl (12 examples)
✅ Loaded v1_l5.pkl (14 examples)
✅ Loaded v1_l6.pkl (48 examples)
✅ Loaded v1_l7.pkl (14 examples)
✅ Loaded v1_l8.pkl (25 examples)
✅ Loaded v1_l9.pkl (9 examples)
✅ Loaded v1_l10.pkl (21 examples)
✅ Loaded v1_l11.pkl (13 examples)
✅ Loaded v1_l12.pkl (18 examples)
✅ Loaded v1_l13.pkl (11 examples)
✅ Loaded v1_l14.pkl (25 examples)
✅ Loaded v1_l15.pkl (16 examples)
✅ Loaded v1_l16.pkl (9 examples)
✅ Loaded v1_l17.pkl (27 examples)
✅ Loaded v1_l18.pkl (18 examples)
✅ Loaded v1_l19.pkl (11 examples)
✅ Loaded v1_l20.pkl (31 examples)
✅ Loaded v1_l21.pkl (9 examples)
✅ Loaded v1_l22.pkl (40 examples)
✅ Loaded v1_l23.pkl (8 examples)
✅ Loaded v1_l24.pkl (28 examples)
✅ Loaded v1_l25.pkl (42 examples)
✅ Loaded v1_l26.pkl (18 examples)
✅ Loaded v1_l27.pkl (24 examples)
✅ Loaded v1_l28.pkl (8 examples)
✅ Loaded v1_l29.pkl (21 examples)
✅ Loaded v1

Map:   0%|          | 0/8 [00:00<?, ? examples/s]

<ipython-input-10-4a23098568a0>:220: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


✅ Eval Accuracy: 0/8 = 0.00
▶︎ Lesson v1_l2.pkl

🔁 Training curriculum level 2


Map:   0%|          | 0/8 [00:00<?, ? examples/s]

...

<ipython-input-10-4a23098568a0>:220: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


✅ Eval Accuracy: 0/32 = 0.00
▶︎ Lesson v4_l46.pkl

🔁 Training curriculum level 345


Map:   0%|          | 0/70 [00:00<?, ? examples/s]

<ipython-input-10-4a23098568a0>:220: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


✅ Eval Accuracy: 0/70 = 0.00

🧪 Final Test Generation:
INPUT : They are <extra_id_0> the car at the <extra_id_1>.
OUTPUT: It it.


In [ ]:
save_dir = "my_syntax_gpt_model"

model.save_pretrained(save_dir)
tokenizer.save_pretrained(save_dir)


('my_syntax_gpt_model/tokenizer_config.json',
 'my_syntax_gpt_model/special_tokens_map.json',
 'my_syntax_gpt_model/spiece.model',
 'my_syntax_gpt_model/added_tokens.json')

In [ ]:
save_dir = "my_syntax_gpt_model"

model = SyntaxT5.from_pretrained(save_dir).to(device)
tokenizer = T5Tokenizer.from_pretrained(save_dir)


# Trec classification

In [ ]:
import os, pickle, torch
from datasets import load_dataset, Dataset
from torch.utils.data import Dataset as TorchDataset
from transformers import (
    T5Tokenizer, T5Config, T5ForConditionalGeneration,
    Trainer, TrainingArguments
)
from sklearn.metrics import accuracy_score, recall_score, f1_score
from tqdm import tqdm
import numpy as np

# ─── Device ───
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

# ─── Tokenizer & Model ───
tokenizer = T5Tokenizer.from_pretrained("t5-base")
label_names = ["ABBR", "ENTY", "DESC", "HUM", "LOC", "NUM"]
label_tokens = [f"<LABEL_{i}>" for i in range(6)]
tokenizer.add_tokens(label_tokens)
model = SyntaxT5.from_pretrained("my_syntax_gpt_model").to(device)
model.resize_token_embeddings(len(tokenizer))
label_map = {i: label_tokens[i] for i in range(6)}  # int → token
inv_label_map = {v: label_names[i] for i, v in label_map.items()}

# ─── Combo utils ───
combo2id, combo_counter = {}, 1
MAX_COMBO_ID, UNKNOWN_COMBO_ID = 1024, 0

def get_combo_id(pos, dep, ner, morph):
    global combo_counter
    key = (pos, dep, ner, morph)
    if key not in combo2id:
        if combo_counter >= MAX_COMBO_ID:
            return UNKNOWN_COMBO_ID
        combo2id[key] = combo_counter
        combo_counter += 1
    return combo2id[key]

def get_char_offset_ner_map(doc):
    ner_map = {}
    for ent in doc.ents:
        for i in range(ent.start_char, ent.end_char):
            ner_map[i] = ent.type
    return ner_map

def extract_combo_ids_from_doc(doc, tokenizer, max_len=64):
    ner_map = get_char_offset_ner_map(doc)
    combo_ids = []
    for sent in doc.sentences:
        for w in sent.words:
            pos, dep = w.upos or "X", w.deprel or "dep"
            morph = w.feats or ""
            start = w.start_char or 0
            ner = ner_map.get(start, "O")
            cid = get_combo_id(pos, dep, ner, morph)
            sub_len = len(tokenizer(w.text).input_ids) - 1
            combo_ids.extend([cid] * sub_len)
            if len(combo_ids) >= max_len:
                break
        if len(combo_ids) >= max_len:
            break
    combo_ids = combo_ids[:max_len]
    combo_ids += [UNKNOWN_COMBO_ID] * (max_len - len(combo_ids))
    return combo_ids

# ─── Load Dataset & Preparsed .pkl ───
trec = load_dataset("CogComp/trec")
with open("trec_train_docs.pkl", "rb") as f: train_docs = pickle.load(f)
with open("trec_test_docs.pkl", "rb") as f:  test_docs  = pickle.load(f)

train_exs, test_exs = [], []
for i, doc in enumerate(train_docs):
    train_exs.append({
        "text": doc.text,
        "coarse_label": trec["train"][i]["coarse_label"],
        "combo_ids": extract_combo_ids_from_doc(doc, tokenizer)
    })
for i, doc in enumerate(test_docs):
    test_exs.append({
        "text": doc.text,
        "coarse_label": trec["test"][i]["coarse_label"],
        "combo_ids": extract_combo_ids_from_doc(doc, tokenizer)
    })

train_ds = Dataset.from_list(train_exs)
test_ds = Dataset.from_list(test_exs)

# ─── Preprocessing ───
def preprocess_clf(examples):
    inputs = [f"{q}" for q in examples["text"]]
    targets = [label_map[l] for l in examples["coarse_label"]]

    model_inputs = tokenizer(inputs, max_length=64, padding="max_length", truncation=True)
    with tokenizer.as_target_tokenizer():
        lbl = tokenizer(targets, max_length=1, padding="max_length", truncation=False)

    model_inputs["labels"] = [
        [seq[0]] + [-100]*(len(seq)-1) for seq in lbl["input_ids"]
    ]
    model_inputs["combo_ids"] = examples["combo_ids"]
    return model_inputs

train_tok = train_ds.map(preprocess_clf, batched=True, remove_columns=["text", "coarse_label", "combo_ids"])
test_tok  = test_ds.map(preprocess_clf, batched=True, remove_columns=["text", "coarse_label", "combo_ids"])
train_tok.set_format("torch")
test_tok.set_format("torch")

# ─── Dataset wrapper ───
class ClfDataset(TorchDataset):
    def __init__(self, ds): self.ds = ds
    def __len__(self): return len(self.ds)
    def __getitem__(self, i):
        ex = self.ds[i]
        return {
            "input_ids": ex["input_ids"],
            "attention_mask": ex["attention_mask"],
            "labels": ex["labels"],
            "combo_ids": ex["combo_ids"]
        }

train_torch = ClfDataset(train_tok)
test_torch = ClfDataset(test_tok)

# ─── Data collator ───
def collate_batch(batch):
    return {
        "input_ids":      torch.stack([b["input_ids"] for b in batch]),
        "attention_mask": torch.stack([b["attention_mask"] for b in batch]),
        "labels":         torch.stack([b["labels"] for b in batch]),
        "combo_ids":      torch.stack([b["combo_ids"] for b in batch]),
    }

from transformers import EvalPrediction

from transformers import EvalPrediction
from sklearn.metrics import accuracy_score, recall_score, f1_score
from sklearn.metrics import accuracy_score, recall_score, f1_score

from sklearn.metrics import accuracy_score, recall_score, f1_score
import numpy as np

def compute_metrics(eval_pred):
    predictions, labels = eval_pred

    # 📌 Handle prediction tuple from Trainer
    if isinstance(predictions, tuple):
        predictions = predictions[0]

    # 📌 If logits are 3D (batch_size, seq_len, vocab_size)
    if predictions.ndim == 3:
        predictions = predictions.argmax(-1)  # take argmax over vocab

    # 📌 Replace -100 label padding with pad_token_id
    labels = np.where(labels == -100, tokenizer.pad_token_id, labels)

    # 📌 Decode
    decoded_preds = tokenizer.batch_decode(predictions, skip_special_tokens=False)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=False)

    y_true = []
    y_pred = []

    print("\n🔎 Sample Predictions (first 5):")

    for i, (pred_str, label_str) in enumerate(zip(decoded_preds, decoded_labels)):
        pred_str = pred_str.strip()
        label_str = label_str.strip()

        pred_tokens = pred_str.split()
        label_tokens = label_str.split()

        # 📌 Strictly take FIRST token only
        pred_first = pred_tokens[0] if pred_tokens else ""
        label_first = label_tokens[0] if label_tokens else ""

        # 📌 Map token to real label
        pred_label = inv_label_map.get(pred_first, "???")
        label_label = inv_label_map.get(label_first, "???")

        y_pred.append(pred_label)
        y_true.append(label_label)

        # 📌 Print first 5 examples
        if i < 5:
            print(f"  ➡️  pred: {pred_first} ({pred_label}) | label: {label_first} ({label_label})")

    acc = accuracy_score(y_true, y_pred)
    recall = recall_score(y_true, y_pred, average="macro")
    f1 = f1_score(y_true, y_pred, average="macro")

    return {
        "accuracy": acc,
        "recall": recall,
        "f1": f1,
    }

# ─── Train ───
args = TrainingArguments(
    output_dir="./t5_trec_labeltok",
    eval_strategy="epoch",            # <- Typo fixed: eval_strategy → evaluation_strategy
    save_strategy="epoch",                   # 🔥 Save checkpoint every epoch
    save_total_limit=1,                      # 🔥 Only keep latest best model (optional but nice)
    load_best_model_at_end=True,             # 🔥 Load the best model automatically at the end
    metric_for_best_model="eval_loss",       # 🔥 Use eval_loss for early stopping
    greater_is_better=False,                 # 🔥 Because lower loss is better
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=10,
    logging_steps=5,
    learning_rate=1e-5,
    # weight_decay=0.01,
    # warmup_ratio=0.1,
    report_to="none",
    remove_unused_columns=False,
    dataloader_pin_memory=False
)

trainer = Trainer(
    model=model,
    args=args,
    compute_metrics=compute_metrics,
    train_dataset=train_torch,
    eval_dataset=test_torch,
    data_collator=collate_batch
)

trainer.train()
trainer.evaluate()

# def classify(question: str, combo_ids: list[int]) -> str:
#     prompt = f"{question}"
#     enc = tokenizer(prompt, return_tensors="pt", max_length=64, padding="max_length", truncation=True)
#     model.stored_combo_ids = torch.tensor([combo_ids], device=device)
#     with torch.no_grad():
#         out = model.generate(
#             input_ids=enc.input_ids.to(device),
#             attention_mask=enc.attention_mask.to(device),
#             max_new_tokens=1,   # 🔥 FORCE only one token
#             do_sample=False,
#             num_beams=1,
#             use_cache=True
#         )
#     decoded = tokenizer.decode(out[0], skip_special_tokens=False).strip()

#     for label_token, label_name in inv_label_map.items():
#         if label_token in decoded:
#             return label_name
#     return "???"



# # ─── Evaluation ───
# y_true, y_pred = [], []
# for ex in test_exs:
#     y_true.append(label_names[ex["coarse_label"]])
#     y_pred.append(classify(ex["text"], ex["combo_ids"]))
#     print(y_true[-1], y_pred[-1])

# print("Accuracy:", accuracy_score(y_true, y_pred))
# print("Recall  :", recall_score(y_true, y_pred, average="macro"))
# print("F1 Score:", f1_score(y_true, y_pred, average="macro"))


Using device: cuda


Map:   0%|          | 0/5452 [00:00<?, ? examples/s]

/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py:3980: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


Map:   0%|          | 0/500 [00:00<?, ? examples/s]


🔎 Sample Predictions (first 5):
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)
  ➡️  pred: <LABEL_2> (DESC) | label: <LABEL_4> (LOC)
  ➡️  pred: <LABEL_3> (HUM) | label: <LABEL_3> (HUM)
  ➡️  pred: <LABEL_2> (DESC) | label: <LABEL_2> (DESC)
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)

🔎 Sample Predictions (first 5):
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)
  ➡️  pred: <LABEL_4> (LOC) | label: <LABEL_4> (LOC)
  ➡️  pred: <LABEL_3> (HUM) | label: <LABEL_3> (HUM)
  ➡️  pred: <LABEL_2> (DESC) | label: <LABEL_2> (DESC)
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)

🔎 Sample Predictions (first 5):
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)
  ➡️  pred: <LABEL_4> (LOC) | label: <LABEL_4> (LOC)
  ➡️  pred: <LABEL_3> (HUM) | label: <LABEL_3> (HUM)
  ➡️  pred: <LABEL_2> (DESC) | label: <LABEL_2> (DESC)
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)

🔎 Sample Predictions (first 5):
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)
  ➡️  pred: <

There were missing keys in the checkpoint model loaded: ['encoder.embed_tokens.weight', 'decoder.embed_tokens.weight', 'lm_head.weight'].



🔎 Sample Predictions (first 5):
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)
  ➡️  pred: <LABEL_4> (LOC) | label: <LABEL_4> (LOC)
  ➡️  pred: <LABEL_3> (HUM) | label: <LABEL_3> (HUM)
  ➡️  pred: <LABEL_2> (DESC) | label: <LABEL_2> (DESC)
  ➡️  pred: <LABEL_5> (NUM) | label: <LABEL_5> (NUM)
NUM LOC
LOC LOC
HUM LOC
DESC LOC
NUM LOC
NUM LOC
HUM LOC
ENTY LOC
DESC LOC
DESC LOC
LOC LOC
HUM LOC
NUM LOC
HUM LOC
NUM LOC
NUM LOC
ENTY LOC
HUM LOC
DESC LOC
NUM LOC
HUM LOC
DESC LOC
LOC LOC
DESC LOC
DESC LOC
HUM LOC
DESC LOC
LOC LOC
LOC LOC
LOC LOC
NUM LOC
LOC LOC
DESC LOC
NUM LOC
NUM LOC
NUM LOC
LOC LOC
NUM LOC
NUM LOC
NUM LOC
ENTY LOC
DESC LOC
DESC LOC
DESC LOC
ENTY LOC
ENTY LOC
NUM LOC
DESC LOC
NUM LOC
HUM LOC
DESC LOC
HUM LOC
HUM LOC
DESC LOC
DESC LOC
DESC LOC
NUM LOC
LOC LOC
LOC LOC
NUM LOC
LOC LOC
HUM LOC
LOC LOC
ENTY LOC
LOC LOC
HUM LOC
ENTY LOC
DESC LOC
NUM LOC
LOC LOC
NUM LOC
NUM LOC
LOC LOC
HUM LOC
LOC LOC
DESC LOC
ENTY LOC
NUM LOC
NUM LOC
HUM LOC
DESC LOC
NUM LOC
HUM LOC
NUM LOC
